# Interactive Data Visualization with Dynamic Maps

This notebook features an interactive dashboard designed to visually analyze data through an intuitive map interface. Users can effortlessly filter data and customize parameters to suit their analysis needs. The map is enriched with a color scale, enhancing the ability to discern variations in the data swiftly. Detailed information about specific data points is conveniently accessible by hovering over individual map cells. The map's interactivity is further amplified with features like zooming, dragging, and selection, providing an engaging and comprehensive data exploration experience.

## Simple plot of the raw data

In [1]:
import geopandas as gpd
import plotly.graph_objects as go
import json


# Load your GeoJSON file
gdf = gpd.read_file('complete.geojson')
gdf = gdf.drop_duplicates()

gdf[['katasterart', 'grundparzelle', 'katastralgemeinde']] = gdf['name'].str.split('_', expand=True)

# Set the original CRS and transform to WGS 84
gdf = gdf.set_crs('epsg:32632', allow_override=True)
gdf_wgs84 = gdf.to_crs(epsg=4326)

# Transform to a projected CRS for centroid calculation
gdf_projected = gdf_wgs84.to_crs(epsg=32632)
centroid_projected = gdf_projected.geometry.centroid
centroid = centroid_projected.to_crs(epsg=4326)

# Convert GeoDataFrame to JSON
geojson = json.loads(gdf_wgs84.to_json())

# Create a map using Plotly Graph Objects
fig = go.Figure(go.Choroplethmapbox(geojson=geojson, 
                                    locations=gdf_wgs84.index, 
                                    z=gdf_wgs84.index,
                                    marker_opacity=0.5
                                    ))

# Set map center
fig.update_layout(mapbox_style="open-street-map",
                  mapbox_center={"lat": centroid.y.mean(), "lon": centroid.x.mean()},
                  mapbox_zoom=11)

# Show the figure
fig.show()

## Add area to the data

In [2]:
gdf['area'] = gdf.geometry.area
# gdf = gdf.sort_values(by='area', ascending=False)
# gdf = gdf.head(40)
# gdf = gdf.reset_index(drop=True)
# gdf

## Read precomputed data from csv_dump containing aggregated data

The data contains information about 
- date, 
- reci, 
- ndwi, 
- ndvi, 
- gdd, 
- tmax, 
- tmin, 
- tmean, 
- pmm, 
- elevation, 
- exposure, 
- slope, 
- katasterart, 
- grundparzelle, 
- katastralgemeinde, 
- name, 
- geometry.

In [3]:
import pandas as pd
import os

# Path to the directory with CSV files
csv_dump_dir = 'csv_dump/'

# List to store all the dataframes
dfs = []

# Iterate over all CSV files in the directory
for filename in os.listdir(csv_dump_dir):
    if filename.endswith('.csv'):
        # Read the CSV file
        file_path = os.path.join(csv_dump_dir, filename)
        df = pd.read_csv(file_path)

        # Parse the filename to extract information
        katasterart, grundparzelle, katastralgemeinde = filename.replace('.csv', '').split('_')
        
        # Add the information as new columns to the dataframe
        df['katasterart'] = katasterart
        df['grundparzelle'] = grundparzelle.replace(".", "")
        df['katastralgemeinde'] = katastralgemeinde

        # Append the dataframe to the list
        dfs.append(df)

# Concatenate all dataframes into a single dataframe
final_df = pd.concat(dfs, ignore_index=True)

final_df.rename(columns={final_df.columns[0]: 'date'}, inplace=True)
final_df['date'] = pd.to_datetime(final_df['date'], format='%Y-%m-%d')

result_inner = pd.merge(final_df, gdf, on=['katasterart', 'grundparzelle', 'katastralgemeinde'], how='inner')
result_inner = result_inner.set_geometry('geometry')
result_inner

date      reci      ndwi      ndvi        gdd       tmax  \
0      2020-03-22  0.273454 -0.009688  0.117313   3.135000  18.806040   
1      2020-04-21       NaN       NaN       NaN   6.160000  21.403164   
2      2020-05-21       NaN       NaN       NaN  10.280001  31.037457   
3      2020-06-20       NaN       NaN       NaN   9.965000  29.271133   
4      2020-07-20       NaN       NaN       NaN  14.625000  33.111153   
...           ...       ...       ...       ...        ...        ...   
137865 2022-08-09       NaN       NaN       NaN  15.270000  32.911438   
137866 2022-09-08       NaN       NaN       NaN  10.510000  24.048079   
137867 2022-10-08  2.374405 -0.344786  0.539131   5.690000  21.805376   
137868 2022-11-07  1.137309 -0.229674  0.361416   0.000000  13.449416   
137869 2022-12-07  1.091407 -0.216860  0.351433   0.000000   7.737581   

             tmin      tmean        pmm  elevation  exposure  slope  \
0        7.469026  12.922198   0.527145        NaN       NaN    NaN   
1       10.919970  15.377550   0.000000        NaN       NaN    NaN   
2        9.525099  21.534718   0.000000        NaN       NaN    NaN   
3       10.659802  21.104099   0.000000        NaN       NaN    NaN   
4       16.137806  24.769104   0.000000        NaN       NaN    NaN   
...           ...        ...        ...        ...       ...    ...   
137865  17.620047  24.409346   0.000000        NaN       NaN    NaN   
137866  16.963907  19.772738  16.837345        NaN       NaN    NaN   
137867   9.577883  14.444611   0.002785        NaN       NaN    NaN   
137868   3.577406   7.680175   0.000000        NaN       NaN    NaN   
137869  -1.297794   0.865345   0.000000        NaN       NaN    NaN   

       katasterart grundparzelle katastralgemeinde          name  \
0                P          2203               621    P_2203_621   
1                P          2203               621    P_2203_621   
2                P          2203               621    P_2203_621   
3                P          2203               621    P_2203_621   
4                P          2203               621    P_2203_621   
...            ...           ...               ...           ...   
137865           P        2884-1               621  P_2884-1_621   
137866           P        2884-1               621  P_2884-1_621   
137867           P        2884-1               621  P_2884-1_621   
137868           P        2884-1               621  P_2884-1_621   
137869           P        2884-1               621  P_2884-1_621   

                                                 geometry         area  
0       POLYGON ((674013.606 5139478.602, 674030.528 5...  3512.632265  
1       POLYGON ((674013.606 5139478.602, 674030.528 5...  3512.632265  
2       POLYGON ((674013.606 5139478.602, 674030.528 5...  3512.632265  
3       POLYGON ((674013.606 5139478.602, 674030.528 5...  3512.632265  
4       POLYGON ((674013.606 5139478.602, 674030.528 5...  3512.632265  
...                                                   ...          ...  
137865  POLYGON ((672846.720 5141868.565, 672847.402 5...  1120.117784  
137866  POLYGON ((672846.720 5141868.565, 672847.402 5...  1120.117784  
137867  POLYGON ((672846.720 5141868.565, 672847.402 5...  1120.117784  
137868  POLYGON ((672846.720 5141868.565, 672847.402 5...  1120.117784  
137869  POLYGON ((672846.720 5141868.565, 672847.402 5...  1120.117784  

[137870 rows x 18 columns]

## Filter data for the last year

this is stille enough or a qualitative analysis and keep performance high

In [4]:
filtered_df = result_inner[result_inner['date'] > pd.Timestamp('2021-07-12')]

## Method create_map_figure

Generates an interactive choropleth map using Plotly based on the provided GeoDataFrame.

Parameters:
filtered_df (GeoDataFrame): A GeoDataFrame containing the geographic data and associated attributes.
tmean_column (str): The name of the column in filtered_df to be used for the choropleth's values.
katastralgemeinde_grundparzelle (str): A string used to filter the data based on 'katastralgemeinde' and 
                                        'grundparzelle' values. It accepts a format 'KG_GP' where 'KG' is the 
                                        value for 'katastralgemeinde' and 'GP' is the value for 'grundparzelle'. 
                                        If 'KG' equals 'top', the top 'GP' unique areas in the 'area' column 
                                        are used for filtering.

The function performs the following steps:
1. Copies the original DataFrame to avoid 'SettingWithCopyWarning'.
2. Filters the data based on the katastralgemeinde and grundparzelle, or by top n areas if specified.
3. Concatenates specified columns for hover text.
4. Sets the Coordinate Reference System (CRS) and transforms to WGS 84 for map plotting.
5. Converts the GeoDataFrame to JSON format for use with Plotly.
6. Initializes a Plotly figure and adds choropleth traces for each unique date.
7. Adds an interactive slider to control the visible date on the map.
8. Updates the layout of the figure with map settings and slider.

Returns:
go.Figure: An interactive Plotly choropleth map figure.

In [5]:
import geopandas as gpd
import plotly.graph_objects as go
import json

def create_map_figure(filtered_df, tmean_column, katastralgemeinde_grundparzelle):
    """
    Generates an interactive choropleth map using Plotly based on the provided GeoDataFrame.

    Parameters:
    filtered_df (GeoDataFrame): A GeoDataFrame containing the geographic data and associated attributes.
    tmean_column (str): The name of the column in filtered_df to be used for the choropleth's values.
    katastralgemeinde_grundparzelle (str): A string used to filter the data based on 'katastralgemeinde' and 
                                           'grundparzelle' values. It accepts a format 'KG_GP' where 'KG' is the 
                                           value for 'katastralgemeinde' and 'GP' is the value for 'grundparzelle'. 
                                           If 'KG' equals 'top', the top 'GP' unique areas in the 'area' column 
                                           are used for filtering.

    The function performs the following steps:
    1. Copies the original DataFrame to avoid 'SettingWithCopyWarning'.
    2. Filters the data based on the katastralgemeinde and grundparzelle, or by top n areas if specified.
    3. Concatenates specified columns for hover text.
    4. Sets the Coordinate Reference System (CRS) and transforms to WGS 84 for map plotting.
    5. Converts the GeoDataFrame to JSON format for use with Plotly.
    6. Initializes a Plotly figure and adds choropleth traces for each unique date.
    7. Adds an interactive slider to control the visible date on the map.
    8. Updates the layout of the figure with map settings and slider.

    Returns:
    go.Figure: An interactive Plotly choropleth map figure.
    """
    # Create a copy of the DataFrame to avoid SettingWithCopyWarning
    df = filtered_df.copy()
    if katastralgemeinde_grundparzelle is not None:
        katastralgemeinde, grundparzelle = katastralgemeinde_grundparzelle.split('_')
        if katastralgemeinde=='top':
            n = int(grundparzelle) + 1
            top_n_areas = filtered_df['area'].unique()
            top_n_areas.sort()  # Sort the values
            top_n_areas = top_n_areas[-n:]  # Get the top n largest unique values

            # Step 3: Find the smallest value among the top n areas
            min_of_top_n = top_n_areas[0]

            # Step 4: Filter the DataFrame
            df = filtered_df[filtered_df['area'] > min_of_top_n].copy()
        else:
            df = df[(df['katastralgemeinde'] == katastralgemeinde) & (df['grundparzelle'] == grundparzelle)]
    else:
        # if the user does not specify anything then we filter by the top 20 areas
        n = 20
        top_n_areas = filtered_df['area'].unique()
        top_n_areas.sort()  # Sort the values
        top_n_areas = top_n_areas[-n:]  # Get the top n largest unique values

        # Step 3: Find the smallest value among the top n areas
        min_of_top_n = top_n_areas[0]

        # Step 4: Filter the DataFrame
        df = filtered_df[filtered_df['area'] > min_of_top_n].copy()

    # Concatenate specified columns for hover text
    columns_to_concatenate = ['date', 'reci', 'ndwi', 'ndvi', 'gdd', 'tmax', 'tmin', 'tmean', 'pmm', 
                              'elevation', 'exposure', 'slope', 'katasterart', 'grundparzelle', 'katastralgemeinde']
    df['hover_text'] = df[columns_to_concatenate].apply(
        lambda x: '<br>'.join(f"{k}: {v}" for k, v in x.items()), axis=1)

    # Set the original CRS and transform to WGS 84
    gdf = df.set_crs('epsg:32632', allow_override=True)
    gdf_wgs84 = gdf.to_crs(epsg=4326)

    gdf_wgs84['date'] = gdf_wgs84['date'].dt.strftime('%Y-%m-%d')

    # Transform to a projected CRS for centroid calculation
    gdf_projected = gdf_wgs84.to_crs(epsg=32632)
    centroid_projected = gdf_projected.geometry.centroid
    centroid = centroid_projected.to_crs(epsg=4326)

    # Convert GeoDataFrame to JSON
    geojson = json.loads(gdf_wgs84.to_json())

    # Initialize the figure
    fig = go.Figure()

    # Define a custom color scale from blue to red
    blue_red_color_scale = [
        [0, 'blue'],        
        [0.5, 'white'],     
        [1, 'red']          
    ]

    # Get the list of unique dates for the slider
    unique_dates = sorted(gdf_wgs84['date'].unique())

    # Determine the min and max values of the specified tmean column
    tmean_min = gdf_wgs84[tmean_column].min()
    tmean_max = gdf_wgs84[tmean_column].max()

    # Create a trace for each date
    for date in unique_dates:
        # Filter the GeoDataFrame for the current date
        gdf_date = gdf_wgs84[gdf_wgs84['date'] == date]
        
        # Create a trace for the filtered GeoDataFrame
        fig.add_trace(
            go.Choroplethmapbox(
                geojson=geojson,
                locations=gdf_date.index,
                z=gdf_date[tmean_column],
                name=date,
                visible=(date == unique_dates[0]),  
                marker_opacity=0.5,
                zmin=tmean_min, 
                zmax=tmean_max,  
                colorbar=dict(title=tmean_column, tickvals=[tmean_min, tmean_max]),
                colorscale=blue_red_color_scale,
                hovertext=gdf_date['hover_text'],  # Set hover text
                hoverinfo="text"  # Display custom hover text
            )
        )

    # Add the slider
    date_steps = []
    for i, date in enumerate(unique_dates):
        step = dict(
            method="update",
            args=[{"visible": [date == d for d in unique_dates]},
                  {"title": f"Date: {date}"}],  
            label=date
        )
        date_steps.append(step)

    sliders = [dict(
        active=0,
        currentvalue={"prefix": "Date: "},
        pad={"t": 50},
        steps=date_steps
    )]

    # Set map center and sliders in the layout
    fig.update_layout(
        mapbox_style="open-street-map",
        mapbox_center={"lat": centroid.y.mean(), "lon": centroid.x.mean()},
        mapbox_zoom=11,
        sliders=sliders,
        height=1000,
        width=1000 
    )

    return fig


# fig = create_map_figure(filtered_df, 'tmean')
# fig.show()

## Interactive Dash Application for Map Visualization with Filtering Capabilities

In [8]:
# Import necessary libraries
import dash
from dash import dcc, html, Input, Output, State
import plotly.graph_objects as go
import geopandas as gpd
import json

# List of column names for the dropdown
dropdown_options = ['reci', 'ndwi', 'ndvi', 'gdd', 'tmax', 'tmin', 'tmean', 'pmm', 
                    'elevation', 'exposure', 'slope']

# Initialize the Dash app
app = dash.Dash(__name__)

# Define the layout of the app
app.layout = html.Div([
    html.H3("Select the Katastralgemeinde and Grundparzelle (format KG_GP or top_n). Example: 621_2156-1 or top_5"),  # Header before the input field
    html.Div([
        dcc.Input(id='input-field', type='text', placeholder='Enter additional parameter')
    ]),
    html.H3("Select the Parameter to Display:"),  # Title above the dropdown
    dcc.Dropdown(
        id='column-selector',
        options=[{'label': i, 'value': i} for i in dropdown_options],
        value='tmean'  # Default value
    ),
    html.Button('Submit', id='submit-button', n_clicks=0),
    html.H3("Map of the area of interest"),  # Title above the dropdown
    dcc.Graph(id='map-plot')
])

# Callback to update the map plot based on dropdown selection and input field
@app.callback(
    Output('map-plot', 'figure'),
    [Input('submit-button', 'n_clicks')],
    [State('column-selector', 'value'),
     State('input-field', 'value')]
)
def update_map(n_clicks, selected_column, katastralgemeinde_grundparzelle):
    fig = create_map_figure(filtered_df, selected_column, katastralgemeinde_grundparzelle)
    return fig

# Run the app
if __name__ == '__main__':
    app.run_server(debug=True, port=5050)
